# Booking.com Data Job Analysis


### Introduction

>**We rely on AI to analyse your CV and enrich it with market data to get a well rounded skill set overview. Consequently, your skills will be matched with the best available career opportunity.**

### Project Objective


### Methodology
- Reading in raw data from web scraper
- Cleaning up data / string manipulation
- Exploratory Analysis to understand data
- Delving into specifics to answer key questions

* In order to create a concise overview of the relevant data, I will opt for creating topic specific dataframes


In [1]:
#Imports
import numpy as np
import pandas as pd

#Settings for string legibility
pd.set_option('display.max_rows', 50)
pd.set_option("display.max_colwidth", -1)

from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

#String manipulations
import re, string

#Visualizations
import matplotlib.pyplot as plt
import seaborn as sns
from collections import Counter
%matplotlib inline
plt.rcParams['figure.figsize'] = [20,16]
plt.rcParams['figure.dpi'] = 300
%config InlineBackend.figure_format = 'svg'
sns.set_style("whitegrid")

#Wordcloud
from wordcloud import WordCloud
from nltk.corpus import stopwords

#Quality of life
import warnings
warnings.filterwarnings('ignore')

/var/folders/_r/ryq2zqs914vb11q08_c9klqc0000gn/T/ipykernel_63549/3844321626.py:7: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option("display.max_colwidth", -1)


In [2]:
df = pd.read_csv('Booking_Jobs.csv')

In [3]:
print('Dataframe shape: ', df.shape)
df.head()

Dataframe shape:  (108, 2)


Job Title  \
0  Data Engineer                                                        
1  Manager Data Science Insights - Content Agency                       
2  Senior Data Engineering Manager - Data & Machine Learning Platform   
3  Senior Data Engineer - Data & Machine Learning Platform              
4  Data Analyst Trip Foundations                                        

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 108 entries, 0 to 107
Data columns (total 2 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Job Title        108 non-null    object
 1   Job Description  108 non-null    object
dtypes: object(2)
memory usage: 1.8+ KB


### Combining Descriptions

We'll start by adding all Data job descriptions together to find the most commonly used words on the Booking.com career site. Doing this will allow us to gain insight into what words the company uses to describe itself, their values, and what they seek in future employees.

In [5]:
all_descriptions = ''.join(description for description in df['Job Description']) #Joining together all descriptions
all_descriptions = all_descriptions.replace('teams','team') #Combining similar words to create fair comparison
all_descriptions = all_descriptions.replace('world.','world')
all_descriptions = all_descriptions.translate(str.maketrans('', '', string.punctuation)) #Removing punctuation
all_descriptions = all_descriptions.lower()

print ("There are {} words in the combined data-related job descriptions.".format(len(all_descriptions))) #Printing results

There are 536907 words in the combined data-related job descriptions.


In [ ]:
word_count = dict(Counter(all_descriptions.split())) #Creating a dictionary of all words in split description
words_popular = {k: v for k, v in sorted(word_count.items(), key=lambda item: item[1], reverse=True)} #Sorting dictionary by most popular words
words_nonstop = [w for w in words_popular if w not in stopwords]
words_popular_nonstop = {k: words_popular[k] for k in words_nonstop if k in words_popular}
words_all_jobs = pd.DataFrame.from_dict(words_popular_nonstop, orient='index',columns=['Count']).reset_index()
words_all_jobs.head(10)

### Filtering out stopwords

To get a more accurate reprentation of which key words matter most we'll filter out common stopwords. Though there are many libraries that provide lists of stopwords on various languages, we'll need to add a few more words that are specific to this platform.

In [6]:
stopwords = sorted(stopwords.words('english')) #Using the Natural Language Toolkit (NLTK) library
stopwords_booking = ['booking','com', 'booking.com', 'bookingcom', 'part', 'right', 'make', 'work', 'working',#Adding platform specific words
                     'need', 'e','g', '&','within', 'well', '-', '.', 'including', 'high', 'role', 'relevant', 
                     'strong', 'key','one', 'year', 'years', 'looking', 'everyone', 'easier', 'sexual', 
                     'orientation','best', 'company', 'B', 'application', 'equal', 'opportunity', 'national', 'world'
                     'origin', 'across', 'able', 'genetic', 'disability', 'new', 'gender', 'identity', 'level']
stopwords.extend(stopwords_booking) #Combining both into a stopwords list

### Wordcloud

One way to make this intuitively insightful is to use a wordcloud, which represents the most commons words in a visual manner. The size of each word corresponds to the frequency of its use.

In [7]:
wordcloud = WordCloud(stopwords=stopwords, min_font_size=8, max_font_size=100, max_words=500, width=800, height=400,prefer_horizontal=.5, background_color="white").generate(all_descriptions)

In [8]:
plt.imshow(wordcloud, interpolation='bilinear')
plt.axis("off")
plt.show()

### What did we learn?

A few words pop out immediately:
- Data
- Experience
- Business
- Team
- Product

These are at the core of the Booking.com business and values, and unsurprisingly so. Having included ALL data-related jobs, we can only spot general trends.


### Bar Chart

Wordclouds are great for getting a sense of what's important, but ranking the top 20 most relevant words becomes more difficult. That's why we use a bar chart to accurately rank and communicate our findings.

index  Count
0  data        742  
1  team        692  
2  experience  657  
3  business    522  
4  product     438  
5  learning    267  
6  world       260  
7  machine     260  
8  skills      227  
9  management  216

In [14]:
plt.barh(range(50), [word_count_dict[w] for w in reversed(words_popular_nonstop[0:50])]) #horizontal bar plot using top 50 words
plt.yticks([x for x in range(50)], reversed(words_popular_nonstop[0:50])) #setting vertical ticks to words to corresponding bar
plt.box(on=None)
plt.title('Most common words in data-related job openings on Booking.com', fontsize=30)
plt.show()

TypeError: unhashable type: 'slice'

### What did we learn?

Having looked only at single words without context we can conclude a few things:
- Through Data and Experience reign supreme there is a massive
- Team and Teams are treated seperately, but should be together - resulting in it becoming the 3rd most common 'word'.

In [ ]:
word_count_dict.get('team') + word_count_dict.get('teams')

In [ ]:
word_count_dict.get('world') + word_count_dict.get('world.')

In [ ]:
sns.barplot(data=zz,x='index',y='Count')

In [ ]:
#I'm trying to group together TEAM mand TEAMS to see what difference that makes
# Make WORDLCOUDS AND PLOTS for SPECIFIC DATA JOBS